<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Introducción" data-toc-modified-id="Introducción-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Introducción</a></span><ul class="toc-item"><li><span><a href="#Objetivos-y-selección-de-robot" data-toc-modified-id="Objetivos-y-selección-de-robot-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Objetivos y selección de robot</a></span></li><li><span><a href="#Como-visualizar-el-documento" data-toc-modified-id="Como-visualizar-el-documento-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Como visualizar el documento</a></span></li></ul></li><li><span><a href="#Configuración" data-toc-modified-id="Configuración-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Configuración</a></span></li><li><span><a href="#Identificación-de-solidos-y-ejes" data-toc-modified-id="Identificación-de-solidos-y-ejes-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Identificación de solidos y ejes</a></span></li><li><span><a href="#Asignación-de-referencias" data-toc-modified-id="Asignación-de-referencias-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Asignación de referencias</a></span></li><li><span><a href="#Matrices-de-paso" data-toc-modified-id="Matrices-de-paso-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Matrices de paso</a></span><ul class="toc-item"><li><span><a href="#Referencias-visualizadas-mediante-matrices-de-paso" data-toc-modified-id="Referencias-visualizadas-mediante-matrices-de-paso-5.1"><span class="toc-item-num">5.1&nbsp;&nbsp;</span>Referencias visualizadas mediante matrices de paso</a></span></li></ul></li><li><span><a href="#Modelo-geométrico-inverso" data-toc-modified-id="Modelo-geométrico-inverso-6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Modelo geométrico inverso</a></span></li><li><span><a href="#Apéndice" data-toc-modified-id="Apéndice-7"><span class="toc-item-num">7&nbsp;&nbsp;</span>Apéndice</a></span></li></ul></div>

# Introducción

## Objetivos y selección de robot

El objetivo de esta tarea es modelar la cinemática de un robot manipulador tipo serie de 6 ejes mediante la resolución analítica del modelo geométrico directo e inverso, mediante la sistemática establecida por *Denavit y Hartenberg*.
<br><br>
Se utilizara MATLAB como herramienta de implementación del robot y del modelo geométrico inverso
<br><br>
Hemos elegido elegido el modelo [IRB 2400](https://new.abb.com/products/robotics/industrial-robots/irb-2400) de la gama de robots industriales de ABB, etiquetado como "el robot industrial más popular", con usos destacados en la soldadura de arco por su gran precisión.
![robot_preview](./images/robot_preview.png)

## Como visualizar el documento

El formato de presentación de este trabajo puede ser un poco distinto a lo que esta acostumbrado el lector habitual así que se resume aqui brevemente la elección y el uso de esta herramienta.
<br><br>
Dicho formato se basa en el proyecto [Jupyter](https://jupyter.org/), en el que proporcionan herramientas open-source para crear tus propios "Jupyter notebook", que no son más que una forma ordenada e interactiva de programar, pero al que se le añaden distintas funcionalidades como el uso de celdas [markdown](https://en.wikipedia.org/wiki/Markdown), que permiten formatear texto, ecuaciones, imágenes, tablas, etc.
<br><br>
En este caso, este cuaderno usa el lenguaje de Python, en concreto la versión 3.7. Su uso nos permite crear visualizaciones potentes e interactivas, además de diversos cálculos. Además, para no perder de vista el objetivo del trabajo, usamos la [API de MATLAB para Python](https://www.mathworks.com/help/matlab/matlab-engine-for-python.html?category=matlab-engine-for-python&s_tid=CRUX_gn_documentation_matlab-engine-for-python), para incrustar celdas de código MATLAB en el cuaderno(notebook).

Así pues, la presentación del trabajo se apoyará en código de Python, que el lector puede ignorar completamente y centrarse en las visualizaciones o echar un vistazo e incluso interactuar con éste. En el caso más probable de estar leyendo el documento desde [NBViewer](https://nbviewer.jupyter.org/) el lector solo podrá interactuar con las visualizaciones, no con el código; lo que no supone ningún incoveniente en este caso. Cabe destacar que el siguiente apartado de configuración puede ser omitido por el lector sin ningún problema, pues solo incluye código para hacer funcionar la API de MATLAB o una serie de funciones y clases para las visualizaciones.
<br><br>
Cuando una celda tenga `%%matlab_magic` como encabezado, quiere decir que esa celda usara código MATLAB. Para las visualizaciones 3D interactivas, se pueden rotar arrastrando con el click izquierdo, desplazar arrastrando con el click derecho y hacer zoom con la ruedecilla del ratón. Si la figura se ha ido de rango, se puede pulsar sobre el icono con forma de casita en la esquina superior derecha de la gráfica.


# Configuración

**Pasar a siguiente sección a no ser que el lector se encuentre especialmente interesado en el código detras de las visualizaciones, entre otras cosas, que nada tienen que ver con la robótica industrial**

Librerias y funciones a usar

In [1]:
# Common imports
import numpy as np
import pandas as pd

#Plotting
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns

#Interactive plotting
import plotly
import plotly.graph_objects as go
from plotly.offline import download_plotlyjs, init_notebook_mode,  iplot
init_notebook_mode(connected=True)

# Interactive widgets
import ipywidgets as widgets

# MATLAB API
import matlab.engine

#Specific
from scipy.spatial.transform import Rotation as Rot

Funcion para incrustar MATLAB en el cuaderno

In [2]:
import io
from IPython.core.magic import register_cell_magic
ip = get_ipython()

out = io.StringIO()
err = io.StringIO()

# Setup matlab cell magic #
@register_cell_magic
def matlab_magic(line,cell):
    out.truncate(0)
    out.seek(0)
    err.truncate(0)
    err.truncate(0)
    raw = r'{line}.eval("""{cell}""", nargout=0, stdout=out, stderr=err)'
    ip.run_cell(raw.format(line=line, cell=cell))
    print(out.getvalue())
    print(err.getvalue())

In [3]:
eng = matlab.engine.start_matlab() # start matlab session
eng.eval("format compact", nargout=0) # compact formatting in matlab's stdout

Plotear referencias

In [4]:
class myAxes():
    def __init__(self, axes_mx=None): #axes_mx is mxn; contains m points and n dimensions
        if axes_mx is None:
            axes_mx = np.array([[0,0,0],[1,0,0],[0,1,0],[0,0,1]])
        self.mx = axes_mx
    def get_points(self):
        return x, y, z
    def move_from_vector(self, u1, u2, units):
        v = u2 - u1
        vnorm = v / np.linalg.norm(v)
        point = u1 + units * vnorm
        return point
    def get_Mesh(self, colors=None, units = 1, numstr=""):
        if colors is None:
            colors = ["rgb(20,20,20)", "rgb(255,0,0)", "rgb(0,255,0)", "rgb(0,0,255)"]
        textfont=dict(size=8, color=colors[0])
        x, y, z = self.mx.T
        points = go.Scatter3d(x = x, y = y, z = z,
                       mode ='markers',
                       marker = dict(size=2, color=colors),
                     )
        x0, y0, z0 = self.mx[0]
        xi, yi, zi = self.move_from_vector(self.mx[0], self.mx[1], units)
        i = go.Scatter3d( x = [x0, xi],y = [y0, yi], z = [z0, zi],
                       mode ='lines+text',
                       text =["", "x"+numstr],
                       textposition="middle right",
                       textfont=textfont,
                       line=dict(width = 2, color=colors[1])
                     )
        xj, yj, zj = self.move_from_vector(self.mx[0], self.mx[2], units)
        j = go.Scatter3d( x = [x0, xj],y = [y0, yj], z = [z0, zj],
                       mode ='lines+text',
                       text =["", "y"+numstr],
                       textposition="middle right",
                       textfont=textfont,
                       line=dict(width = 2, color=colors[2])
                     )
        xk, yk, zk = self.move_from_vector(self.mx[0], self.mx[3], units)
        k = go.Scatter3d( x = [x0, xk],y = [y0, yk], z = [z0, zk],
                       mode ='lines+text',
                       text =["", "z"+numstr],
                       textposition="middle right",
                       textfont=textfont,
                       line=dict(width = 2, color=colors[3])
                     )
        data = [points, i, j, k]
        return data
        

Plotear cilindros

In [5]:
class myCylinder():
    def __init__(self, r=1, h=1, nt=100, nv=50):
        theta = np.linspace(0, 2*np.pi, nt)
        v = np.linspace(-h/2, h/2, nv )
        theta, v = np.meshgrid(theta, v)
        self.x = r*np.cos(theta) 
        self.y = r*np.sin(theta) 
        self.z = v
    def get_points(self):
        return x, y, z
    def get_Mesh(self, colorscale=None, opacity=0.5):
        if colorscale is None:
            colorscale = [[0, 'blue'], [1, 'blue']]
        cyl = go.Surface(x=self.x, y=self.y, z=self.z,
                 colorscale = colorscale,
                 showscale=False,
                 opacity=opacity)
    

Leer las piezas 3D y convertirlas a objetos a plotear

In [6]:
def to_mesh3d(odata):
    # odata is the string read from an obj file
    vertices = []
    faces = []
    lines = odata.splitlines()   
    
    for line in lines:
        slist = line.split()
        if slist:
            if slist[0] == 'v':
                vertex = np.array(slist[1:], dtype=float)
                vertices.append(vertex)
            elif slist[0] == 'f':
                face = []
                for k in range(1, len(slist)):
                    face.append([int(s) for s in slist[k].replace('//','/').split('/')])
                if len(face) > 3: # triangulate the n-polyonal face, n>3
                    faces.extend([[face[0][0]-1, face[k][0]-1, face[k+1][0]-1] for k in range(1, len(face)-1)])
                else:    
                    faces.append([face[j][0]-1 for j in range(len(face))])
            else: pass
    
    
    return np.array(vertices), np.array(faces) 

In [7]:
links_str = []
for link in range(1,14):
    path = './cad_models/o' + str(link) +'.obj'
    with open(path, 'r') as file:
        links_str.append(file.read())

In [8]:
links_arr = []

for link in range(13):
    arr = to_mesh3d(links_str[link])
    links_arr.append(arr)

In [9]:
palette = plotly.colors.qualitative.Plotly
colors = [palette[i] for i in (0,1,2,2,2,3,4,5,6,6,6,1,1)]

In [10]:
links_mesh = []

for link in range(13):
    vertices, faces = links_arr[link]
    x, y, z = vertices.T
    I, J, K = faces.T
    name = 'Link' + str(link)
    mesh = go.Mesh3d(x=x, y=y, z=z, i=I, j=J, k=K, name='', showscale=False, color=colors[link])
    links_mesh.append(mesh)

# Identificación de solidos y ejes

Para identificar los sólidos, podemos usar una visualización 3D, asignando un color a cada sólido:

In [11]:
rng = 1000
layout_r = go.Layout(title='ABB IRB-2400',
                   font=dict(size=14, color='black'),
                   width=900,
                   height=800,
                   scene=dict(xaxis=dict(visible=True, range=[-rng, rng]),
                              yaxis=dict(visible=True, range=[-rng, rng]),  
                              zaxis=dict(visible=True, range=[0, 2000]), 
                              camera=dict(eye=dict(x=1.25, y=1.25, z=0.7)),
                        ), 
                  paper_bgcolor='rgb(255,255,255)',
                  margin=dict(t=80)) 

In [12]:
fig = go.Figure(data=links_mesh[:13], layout=layout_r)
fig.update_layout(scene_aspectmode='cube')
iplot(fig)

En esta visualización, hemos coloreado cada uno de los seis+uno sólidos con un color distinto. Cabe destacar que el sólido cero es un apéndice de la tierra y que se corresponde con $n=0$, como veremos mas adelante en el enfoque sistemático de *Denavit y Hartenberg*. Es decir, tenemos siete solidos(de $0$ a $n$) y seis articulaciones(de $1$ a $n$)
<br><br>
La obtención de los ejes es igualmente trivial una vez localizados los solidos. Aqui una imagen del *datasheet* del robot:
![robot_axis](./images/robot_axis.png)

In [13]:
pd.read_csv('./docs/axes.csv')

Descripcion Posicion Tipo
0       Eje 1        A  Rot
1       Eje 2        B  Rot
2       Eje 3        C  Rot
3       Eje 4        D  Rot
4       Eje 5        E  Rot
5       Eje 6        F  Rot

# Asignación de referencias

Como bien se ha mencionado ya, utilizaremos el algoritmo de Denavit Hartenberg para la obtencióndel modelo cinemático directo. Así pues, para llevar a cabo el proceso, podemos hacer un boceto con las referencias para todos los sólidos siguiendo el metodo de D-H.
<br><br>
A grandes rasgos y tomando como referencia el libro ["Fundamentos de robotica(Barrientos)"](https://www.amazon.es/FUNDAMENTOS-ROBOTICA-ED-Antonio-Barrientos/dp/8448156366) hay que:
>  
- Para $i$ de 0 a $n-1$ situar el eje $\mathbf{z}_i$ sobre el eje de la articulación $i+1$.  
- Para $i$ de 1 a $n-1$, situar el origen del sistema $\left \{ S_{i} \right \}$ (solidario al eslabón i) en la intersección del eje $\mathbf{z}_i$ con la línea normal común a $\mathbf{z}_{i-1}$ y $\mathbf{z}_i$.
- Situar $\mathbf{x}_i$ en la línea normal común a $\mathbf{z}_{i-1}$ y $\mathbf{z}_i$.
- Situar $\mathbf{y}_i$ de modo que forme un sistema dextrógiro con $\mathbf{x}_i$ y $\mathbf{z}_i$.

Así pues, teniendo en cuenta estos factores y el resto pertinentes al algoritmo, damos lugar con las siguientes referencias:

![boceto referencias](./images/boceto_ref1.jpg)

Una vez obtenidos las referencias, podemos elaborar la tabla del algoritmo de D-H. El uso de estos parámetros se describira detalladamente en la próxima sección, pero uno ya puede imaginar que nos servirá para elaborar una serie de transformaciones lineales.
<br><br>
Para ello, se presentan dos imagenes; la primera escribe sobre el boceto anterior y detalla todos los parámetros de forma cualitativa y ayuda a obtener una vision global. La segunda presenta de forma más precisa dichos parámetros(omitiendo algun valor por visibilidad) usando y escribiendo en los esquemas 2D proporcionados por el fabricante.

![boceto dh](./images/boceto_dh.jpg)

![drawing tabla](./images/drawing_tabla.jpg)

Podemos pues, con ambos dibujos, obtener la tabla de *Denavit y Hartenberg*:

In [14]:
d_i = [615,   0,   0, 754,   0, 85]
a_i = [100, 705, 135,   0,   0,  0]
al_i = [-90,  0, -90,  90, -90,  0] # degrees

dh_dict = {r'$\theta_i$':["($\theta_{}$)".format(i) for i in range(1,6+1)],
            r'$d_i$':["${}$".format(d_i[i]) for i in range(6)],
            r'$a_i$':["${}$".format(a_i[i]) for i in range(6)],
            r'$\alpha_i$':["${}".format(al_i[i]) +r"^{o}$" for i in range(6)]
           }
dh_table = pd.DataFrame(dh_dict, index=range(1,7))
dh_table

$\theta_i$  $d_i$  $a_i$ $\alpha_i$
1  ($\theta_1$)  $615$  $100$  $-90^{o}$
2  ($\theta_2$)    $0$  $705$    $0^{o}$
3  ($\theta_3$)    $0$  $135$  $-90^{o}$
4  ($\theta_4$)  $754$    $0$   $90^{o}$
5  ($\theta_5$)    $0$    $0$  $-90^{o}$
6  ($\theta_6$)   $85$    $0$    $0^{o}$

Donde los elementos señalados con $\left ( \bigodot  \right )$ son *variables*. No es sorpresa que todas las coordenadas articulares vengan dadas por $\theta_i$, pues estamos trabajando con un robot de *morfología angular*.
<br><br>
Podemos, además, fijándonos en el dibujo, establecer la posicion de reposo en coordenadas articulares como
$$\mathbf{\theta} = \left ( 0, -90^{o}, 0, 0, 0, 0 \right ) ^{T}$$
donde $\theta_i$ corresponde a la coordenada articular $i$ del vector columna de $\mathbf\theta$.

Es conveniente pasar la tabla de parámetros al espacio de MATLAB en forma de matriz:

In [15]:
tabla_dh_num = np.array([d_i, a_i, al_i]) # formamos el array en python
eng.workspace["tabla_dh_num"] = matlab.double(tabla_dh_num.tolist()) # pasamos la matriz a MATLAB

Note como la siguiente celda tiene encabezado `%%matlab_magic eng` denotando que es una celda con código MATLAB(eng simplemente es la instancia del entorno de matlab)

In [16]:
%%matlab_magic eng

% Pasamos a radianes alfa
tabla_dh_num(3,:) = deg2rad(tabla_dh_num(3,:));
tabla_dh_num

tabla_dh_num =
  615.0000         0         0  754.0000         0   85.0000
  100.0000  705.0000  135.0000         0         0         0
   -1.5708         0   -1.5708    1.5708   -1.5708         0




Nuestra tabla estaría incompleta sin añadir los $\theta_i$, así que podemos usar símbolos para representarlos en MATLAB

In [17]:
%%matlab_magic eng

syms th1 th2 th3 th4 th5 th6
thetas = [th1 th2 th3 th4 th5 th6];
tabla_dh_num  = [ thetas; tabla_dh_num]

tabla_dh_num =
[   th1, th2,   th3,  th4,   th5, th6]
[   615,   0,     0,  754,     0,  85]
[   100, 705,   135,    0,     0,   0]
[ -pi/2,   0, -pi/2, pi/2, -pi/2,   0]




Sin embargo, con el objetivo de obtener una visión intuitiva de los resultados finales dejaremos parte de los parámetros de forma simbólica, tal y como se ve en la siguiente tabla, solo sustituyendo cuando convenga:

In [18]:
%%matlab_magic eng

syms d1 d4 d6;
dis = [d1 0 0 d4 0 d6];
syms a1 a2 a3;
ais = [a1 a2 a3 0 0 0];
alphas = tabla_dh_num(4,:); % todas alfas sustituidas

tabla_dh  = [ thetas; dis; ais; alphas]

tabla_dh =
[   th1, th2,   th3,  th4,   th5, th6]
[    d1,   0,     0,   d4,     0,  d6]
[    a1,  a2,    a3,    0,     0,   0]
[ -pi/2,   0, -pi/2, pi/2, -pi/2,   0]




# Matrices de paso

Hasta el momento, hemos hallado de una forma sistemática las referencias y los parámetros de la tabla D-H, aquí se comenta brevemente el motivo de esta elección y el resultado que se obtiene.
<br><br>
En general, una matriz de transformación homogénea queda definida por 6 grados de libertad, pero el método de Denavit-Hartenberg, permite, en eslabones
rígidos, reducir éste a 4 con la correcta elección de los sistemas de coordenadas.
<br><br>
Por lo tanto, si definimos los sistemas como dicta el algoritmo, para pasar del sistema $\left \{ S_{i-1} \right \}$ al $\left \{ S_{i} \right \}$ necesitamos:<br>
<ul>
    <li> Rotación alrededor del eje $\mathbf{z}_{i-1}$ un ángulo $\theta_{i}$, para que $\mathbf{x}_{i-1}$ y $\mathbf{x}_{i}$ queden paralelos. </li>
    <li> Traslación a lo largo de $\mathbf{z}_{i-1}$ una distancia $d_i$; vector $\mathbf{d}_{i}(0,0,d_i)$, para que $\mathbf{x}_{i-1}$ y $\mathbf{x}_{i}$         queden alineados. </li>
    <li> Traslación a lo largo de $\mathbf{x}_{i}$ una distancia $a_i$; vector $\mathbf{a}_{i}(a_i,0,0)$, para que los origenes de $\left \{ S_{i-1} \right         \}$ y $\left \{ S_{i} \right \}$ coincidan.</li>
    <li> Rotación alrededor del eje $\mathbf{x}_i$ un ángulo $\alpha_i$, para que el nuevo $\left \{ S_{i-1} \right \}$ coincida totalmente con $\left \{         S_{i} \right \}$. </li>
</ul>
Expreasdo de forma matemática:
$$ ^{i-1} \mathbf{A}_{i}=\mathbf{Rotz}\left(\theta_{i}\right) \mathbf{T}\left(0,0, d_{i}\right) \mathbf{T}\left(a_{i} 0,0\right) \mathbf{Rotx}\left(\alpha_{i}\right) $$

A partir de aqui, usaremos codigo MATLAB para hallar las matrices de paso, en ocasiones haciendo uso del [módulo de transformaciones homogéneas](https://www.mathworks.com/help/robotics/coordinate-system-transformations.html?s_tid=CRUX_lftnav) de la "Robotics Systems Toolbox", así como de operaciones simbólicas.

In [19]:
%%matlab_magic eng

% Definimos simbolos theta, d, a, alpha
syms th d a al 

% Transformaciones D-H
Rotz = [cos(th) -sin(th) 0 0; sin(th) cos(th) 0 0; 0 0 1 0; 0 0 0 1]
Td = [1 0 0 0; 0 1 0 0; 0 0 1 d; 0 0 0 1]
Ta = [1 0 0 a; 0 1 0 0; 0 0 1 0; 0 0 0 1]
Rotx = [1 0 0 0; 0 cos(al) -sin(al) 0; 0 sin(al) cos(al), 0; 0 0 0 1]

Rotz =
[ cos(th), -sin(th), 0, 0]
[ sin(th),  cos(th), 0, 0]
[       0,        0, 1, 0]
[       0,        0, 0, 1]
Td =
[ 1, 0, 0, 0]
[ 0, 1, 0, 0]
[ 0, 0, 1, d]
[ 0, 0, 0, 1]
Ta =
[ 1, 0, 0, a]
[ 0, 1, 0, 0]
[ 0, 0, 1, 0]
[ 0, 0, 0, 1]
Rotx =
[ 1,       0,        0, 0]
[ 0, cos(al), -sin(al), 0]
[ 0, sin(al),  cos(al), 0]
[ 0,       0,        0, 1]




La expresion generalizada entonces de $^{i-1} \mathbf{A}_{i}$ viene dada por

In [20]:
%%matlab_magic eng
Tref = Rotz * Td * Ta * Rotx

Tref =
[ cos(th), -cos(al)*sin(th),  sin(al)*sin(th), a*cos(th)]
[ sin(th),  cos(al)*cos(th), -sin(al)*cos(th), a*sin(th)]
[       0,          sin(al),          cos(al),         d]
[       0,                0,                0,         1]




Formateando,

$$^{i-1} \mathbf{A}_{i}=\left[\begin{array}{cccc}
C \theta_{i} & -C \alpha_{i} S \theta_{i} & S \alpha_{i} S \theta_{i} & a_{i} C \theta_{i} \\
S \theta_{i} & C \alpha_{i} C \theta_{i} & -S \alpha_{i} C \theta_{i} & a_{i} S \theta_{i} \\
0 & S \alpha_{i} & C \alpha_{i} & d_{i} \\
0 & 0 & 0 & 1
\end{array}\right]$$

donde $C$ y $S$ representan la funcion coseno y seno, respectivamente.
<br><br>
Hallemos pues con los datos de la tabla y la *matriz de paso de referencia* que acabamos de obtener, las distintas transformaciones para todos los sólidos:

In [21]:
%%matlab_magic eng

for i = 1:6
    disp("Matriz de referencia " + (i-1) + " a " + i)
    param = tabla_dh(:,i).'; % Vector de parametros correspondientes al sólido
    trans = subs(Tref, [th, d, a, al], param) % Transformación para ese solido, susituyendo
                                              % param en Tref
    T(:,:,i) = trans;                         % Matriz con distintas páginas, una para cada sólido
    fprintf(char(10))                         % Da salto de linea(visualizacion)
end

Matriz de referencia 0 a 1
trans =
[ cos(th1),  0, -sin(th1), a1*cos(th1)]
[ sin(th1),  0,  cos(th1), a1*sin(th1)]
[        0, -1,         0,          d1]
[        0,  0,         0,           1]

Matriz de referencia 1 a 2
trans =
[ cos(th2), -sin(th2), 0, a2*cos(th2)]
[ sin(th2),  cos(th2), 0, a2*sin(th2)]
[        0,         0, 1,           0]
[        0,         0, 0,           1]

Matriz de referencia 2 a 3
trans =
[ cos(th3),  0, -sin(th3), a3*cos(th3)]
[ sin(th3),  0,  cos(th3), a3*sin(th3)]
[        0, -1,         0,           0]
[        0,  0,         0,           1]

Matriz de referencia 3 a 4
trans =
[ cos(th4), 0,  sin(th4),  0]
[ sin(th4), 0, -cos(th4),  0]
[        0, 1,         0, d4]
[        0, 0,         0,  1]

Matriz de referencia 4 a 5
trans =
[ cos(th5),  0, -sin(th5), 0]
[ sin(th5),  0,  cos(th5), 0]
[        0, -1,         0, 0]
[        0,  0,         0, 1]

Matriz de referencia 5 a 6
trans =
[ cos(th6), -sin(th6), 0,  0]
[ sin(th6),  cos(th6), 0,  0]
[        

Una vez halladas las transformaciones para pasar de una referencia a la siguiente, es cuestión de componerlas para obtener el modelo geométrico directo.
<br><br>
Además de $ \mathbf{^{0}T_6}$, correspondiente al modelo geométrico directo, calcularemos $\mathbf{^{0}T_3}$ y $\mathbf{^{4}T_6}$, que nos servirán para la resolucion del *modelo geométrico inverso*.

In [22]:
%%matlab_magic eng

Tcomp = eye(4);
for i = 1:6
    Tcomp = Tcomp * T(:,:,i);
end
T06 = Tcomp;

y sustituyendo los parámetros conocidos:

In [23]:
%%matlab_magic eng

T06_num = subs(T06, [dis, ais, alphas], [tabla_dh_num(2,:), tabla_dh_num(3,:), tabla_dh_num(4,:)]);

Hemos decidido no imprimir en pantalla el resultado dado su enorme tamaño(consultar apéndice para ello).
<br><br>
Las dos matrices restantes son:

In [24]:
%%matlab_magic eng

Tcomp = eye(4);
for i = 1:3
    Tcomp = Tcomp * T(:,:,i);
end
T03 = simplify(Tcomp)

T03 =
[ cos(th2 + th3)*cos(th1),  sin(th1), -sin(th2 + th3)*cos(th1), cos(th1)*(a1 + a3*cos(th2 + th3) + a2*cos(th2))]
[ cos(th2 + th3)*sin(th1), -cos(th1), -sin(th2 + th3)*sin(th1), sin(th1)*(a1 + a3*cos(th2 + th3) + a2*cos(th2))]
[         -sin(th2 + th3),         0,          -cos(th2 + th3),            d1 - a3*sin(th2 + th3) - a2*sin(th2)]
[                       0,         0,                        0,                                               1]




y sustituyendo los parámetros conocidos:

In [25]:
%%matlab_magic eng

T03_num = subs(T03, [dis, ais, alphas], [tabla_dh_num(2,:), tabla_dh_num(3,:), tabla_dh_num(4,:)])

T03_num =
[ cos(th2 + th3)*cos(th1),  sin(th1), -sin(th2 + th3)*cos(th1), cos(th1)*(135*cos(th2 + th3) + 705*cos(th2) + 100)]
[ cos(th2 + th3)*sin(th1), -cos(th1), -sin(th2 + th3)*sin(th1), sin(th1)*(135*cos(th2 + th3) + 705*cos(th2) + 100)]
[         -sin(th2 + th3),         0,          -cos(th2 + th3),            615 - 705*sin(th2) - 135*sin(th2 + th3)]
[                       0,         0,                        0,                                                  1]




Que corresponde a $\mathbf{^{0}T_3}$

In [26]:
%%matlab_magic eng

Tcomp = eye(4);
for i = 4:6
    Tcomp = Tcomp * T(:,:,i);
end
T46 = simplify(Tcomp)

T46 =
[ cos(th4)*cos(th5)*cos(th6) - sin(th4)*sin(th6), - cos(th6)*sin(th4) - cos(th4)*cos(th5)*sin(th6), -cos(th4)*sin(th5), -d6*cos(th4)*sin(th5)]
[ cos(th4)*sin(th6) + cos(th5)*cos(th6)*sin(th4),   cos(th4)*cos(th6) - cos(th5)*sin(th4)*sin(th6), -sin(th4)*sin(th5), -d6*sin(th4)*sin(th5)]
[                              cos(th6)*sin(th5),                               -sin(th5)*sin(th6),           cos(th5),      d4 + d6*cos(th5)]
[                                              0,                                                0,                  0,                     1]




y sustituyendo los parámetros conocidos:

In [27]:
%%matlab_magic eng

T46_num = subs(T46, [dis, ais, alphas], [tabla_dh_num(2,:), tabla_dh_num(3,:), tabla_dh_num(4,:)])

T46_num =
[ cos(th4)*cos(th5)*cos(th6) - sin(th4)*sin(th6), - cos(th6)*sin(th4) - cos(th4)*cos(th5)*sin(th6), -cos(th4)*sin(th5), -85*cos(th4)*sin(th5)]
[ cos(th4)*sin(th6) + cos(th5)*cos(th6)*sin(th4),   cos(th4)*cos(th6) - cos(th5)*sin(th4)*sin(th6), -sin(th4)*sin(th5), -85*sin(th4)*sin(th5)]
[                              cos(th6)*sin(th5),                               -sin(th5)*sin(th6),           cos(th5),     85*cos(th5) + 754]
[                                              0,                                                0,                  0,                     1]




Que corresponde a $\mathbf{^{4}T_6}$
<br><br>

## Referencias visualizadas mediante matrices de paso

Podemos pasar ahora a "comprobar" visualmente la posición de las referencias mediante un gráfico 3D como los anteriores, pero calculando matemáticamente la posición absoluta de las referencias para la configuración de reposo.
<br><br>
Empezamos definiendo los puntos que determinan el sistema de coordenadas absoluto OXYZ, sin olvidar la cuarta componente para poder aplicarle las transformaciones homogeneas que hemos calculado:

In [28]:
%%matlab_magic eng

reposo = [0 -pi/2 0 0 0 0];
oxyz = [0 0 0 1; 1 0 0 1; 0 1 0 1; 0 0 1 1].'

oxyz =
     0     1     0     0
     0     0     1     0
     0     0     0     1
     1     1     1     1




Y vamos aplicando las transformaciones sucesivas a OXYZ para obtener los distintos sistemas de coordenadas correspondiente con cada sólido.

In [29]:
%%matlab_magic eng

comp_acumulada = eye(4);  % composicion acumulada hasta el momento
refs(:,:,1) = oxyz;       % refs guarda la posicion de los versores tras cada transformación
for i = 1:6
    comp_acumulada = comp_acumulada * T(:,:,i);
    comp_numerica = subs(comp_acumulada, [thetas, dis, ais, alphas], [reposo, tabla_dh_num(2,:), tabla_dh_num(3,:), tabla_dh_num(4,:)]);
    refs(:,:,i+1) = comp_numerica * oxyz;
end

Hemos hallado pues las coordenadas de los siete sistemas de referencia identificando las componentes de sus versores:

In [30]:
%%matlab_magic eng
refs

refs(:,:,1) =
     0     1     0     0
     0     0     1     0
     0     0     0     1
     1     1     1     1
refs(:,:,2) =
   100   101   100   100
     0     0     0     1
   615   615   614   615
     1     1     1     1
refs(:,:,3) =
         100         100         101         100
           0           0           0           1
        1320        1321        1320        1320
           1           1           1           1
refs(:,:,4) =
         100         100         100         101
           0           0          -1           0
        1455        1456        1455        1455
           1           1           1           1
refs(:,:,5) =
         854         854         855         854
           0           0           0           1
        1455        1456        1455        1455
           1           1           1           1
refs(:,:,6) =
         854         854         854         855
           0           0          -1           0
        1455        1456      

A partir de aqui se usará codigo python para la visualización, así que salte directamente allí, a no ser que le interese ver el proceso.

In [31]:
refs = np.array( [eng.eval("refs(:,:,{})".format(i)) for i in range(1,7+1)] )

In [32]:
axes = [myAxes(refs[i,:3].T).get_Mesh(units=200, numstr=str(i)) for i in range(7)]

In [33]:
#Para evitar solapamiento de texto
axes[5][1].textposition = "top right"
axes[5][3].textposition = "top right"
#Para evitar solapamiento con el plano XY
axes[0][1].textposition = "middle left"
axes[0][2].textposition = "middle left"

In [34]:
trans_mesh = []

for link in range(13):
    vertices, faces = links_arr[link]
    x, y, z = vertices.T
    I, J, K = faces.T
    name = 'Link' + str(link)
    mesh = go.Mesh3d(x=x, y=y, z=z, i=I, j=J, k=K, name='', showscale=False, opacity=0.1, color=colors[link])
    trans_mesh.append(mesh)

In [35]:
rng = 1100
layout_r2 = go.Layout(title='Referencias y matrices de paso',
                   font=dict(size=14, color='black'),
                   width=900, height=800,
                   scene=dict(xaxis=dict(range=[-rng, rng]),
                              yaxis=dict(range=[-rng, rng]),  
                              zaxis=dict(range=[-200, 2000 ]), 
                              camera=dict(eye=dict(x=1., y=1., z=0.6))),
                   showlegend=False,
                   uniformtext_minsize=3,
                   margin=dict(t=80)) 

In [36]:
data = [scatter for scatters in axes for scatter in scatters] + trans_mesh

fig = go.Figure(data=data, layout=layout_r2)
fig.update_layout(scene_aspectmode='cube')
iplot(fig)

Se anima al lector a visualizar pausadamente esta figura, que demuestra la eficiencia del algoritmo y, por otra parte, verifica que la posición cualitativa que habíamos asociado en el boceto se corresponde con unas coordenadas reales, como era de esperar.
<br><br>

# Modelo geométrico inverso

El objetivo del problema cinemático inverso consiste en encontrar los valores que deben adoptar las coordenadas articulares del robot $\mathbf{q}$ en función de una posición y orientación dadas por el usuario, por ejemplo en forma de matriz homogénea($\mathbf{q}$,[$\mathbf{n, o, a}$]). Si bien es cierto que existen soluciones numéricas, su velocidad de convergencia e incluso su convergencia en sí no esta siempre garantizada. Es por ello que se busca una solución cerrada que resuelva el problema:
$$\mathbf{q}=\mathbf{f^{-1}} \left( x,y,z,\phi,\theta,\psi \right)$$
En un primer intento de resolver este problema, uno podría rápidamente pensar dos metodos bastante intuitivos; El primero, de forma geométrica y, el segundo mediante transformaciones inversas al modelo directo, ambos con solución cerrada. Sin embargo, presentan cierta complejidad para un robot de seis grados de libertad.
<br><br>
Una ingeniosa observación surge para aquellos robots en los que los ejes de los tres ultimos grados de libertad se cortan en un mismo punto, llamado de forma informal *muñeca del robot*, que consiste en darse cuenta que la posición de dicho punto muñeca no se ve alterado por los tres últimos grados de libertad, y que solo los tres primeros lo harán. Esta condición se cumple matemáticamente si los parámtetros $a_4, a_5, d_5$ son $0$.
<br>
Antes de explicar en mas detalle este método(llamado desacoplo cinemático), es importante asegurarnos que el robot que se esta analizando cumple dicha condición: Se observa que los ejes $\mathbf{z_3}$, $\mathbf{z_4}$ y $\mathbf{z_5}$ se cortan en un mismo punto, correspondiente al origen de los sistemas $\left\{ S_4 \right\}$ y $\left\{ S_5 \right\}$: $O_4$ y $O_5$ respectivamente. Por su parte, el extremo del robot se situará el origen del sistema $\left\{ S_6 \right\}$: $O_6$.
<br>
Definiendo $\mathbf{p}_m=\overrightarrow{O_0 O_5}$ y $\mathbf{p}_r=\overrightarrow{O_0 O_6}$ como los puntos que van desde el origen del robot hasta el *punto muñeca* y fin del robot, respectivamente; podemos hallar la siguiente relación, donde todos los vectores están referidos a las coordenadas del sistema $\left\{ S_0 \right\}$:
$$\mathbf{p}_m=\mathbf{p}_r -d_6\mathbf{z_6}$$
pues la dirección del eje $\mathbf{z_5}$ y $\mathbf{z_6}$ coinciden y la distancia entre $O_5$ y $O_6$ a lo largo de $\mathbf{z_5}$ es precisamente $d_6$.
<br>
Sabiendo todo esto, queda sólo concluir que cumpliendose la condición de que exista un *punto muñeca*, podemos "desacoplar"(separar) la resolucion del problema cinemática directo en dos fases: la primera para la posición del punto muñeca y la segunda para la orientación deseada.
<br><br>
Se procede pues a hallar la posición de la muñeca en función de las tres primeras variables articulares aplicando el método desacoplado de *Pieper*, tal y como se muestra en la siguiente ecuación:
$$ \mathbf{p}_m= \textit{pos}(\mathbf{^{0}T}_{1} \mathbf{^{1}T}_{2}\mathbf{^{2}T}_{3}\textit{T}(0,0,d_{4}))$$
donde $\mathbf{p}_m$ es el vector de elementos $\left\{ m_x, m_y, m_z \right\}$, correspondientes a una localización general de la muñeca y pos extrae el vector $\mathbf{p}$ de la matriz de transformación.

In [37]:
%%matlab_magic eng

syms mx my mz

transf = T03*transl(0,0,d4);
eqs = transf(1:3,4)

eqs =
 cos(th1)*(a1 + a3*cos(th2 + th3) + a2*cos(th2)) - d4*sin(th2 + th3)*cos(th1)
 sin(th1)*(a1 + a3*cos(th2 + th3) + a2*cos(th2)) - d4*sin(th2 + th3)*sin(th1)
                     d1 - d4*cos(th2 + th3) - a3*sin(th2 + th3) - a2*sin(th2)




Vamos a proceder pues a una resolución analítica del siguiente sistema de ecuaciones:<br><br>
$$  \left\{\begin{matrix}
C_1\left ( a_1 + a_3C_{23}+a_2C_2-d_4S_{23} \right ) = m_x
\\
S_1\left ( a_1 + a_3C_{23}+a_2C_2-d_4S_{23} \right ) = m_y \tag{6.1, 6.2 y 6.3}
\\ 
d_1 - d_4C_{23}-a_3S_{23}-a_2S_2 = m_z
\end{matrix}\right. 
$$
Si despejamos $C_1$ y $S_1$ de las dos primeras expresiones tenemos
$$ C_1 \frac{m_x}{a_1 + a_3C_{23}+a_2C_2-d_4S_{23}} \tag{6.4} $$
$$ S_1= \frac{m_y}{a_1 + a_3C_{23}+a_2C_2-d_4S_{23}} \tag{6.5} $$
dividiendo la segunda ecuación(6.5) entre la primera(6.4) y despejando $\theta_1$
$$ \frac{S_1}{C_1} = \frac{m_y}{m_x}$$
$$ \theta_1 = \textit{atan2}\left(my, mx\right) \tag{6.6}$$
por lo que ya hemos resuelto la primera variable articular. Para la segunda, tomamos del sistema inicial la primera ecuación(6.1) y la tercera(6.3), donde reordenando sus términos tenemos
$$ a_3C_{23}-d_4S_{23} = \frac{m_x}{C_1}-a_2C_2 -a_1 \tag{6.6}$$
$$ a_3S_{23} +d_4C_{23} = d_1 -a_2S_2-m_z \tag{6.7}$$

In [94]:
%%matlab_magic eng

th1_s1 = solve(C1_left_mem(3,4) == C1_right_mem(3,4), th1)

th1_s1 =
  -log(((pmx^2*sin(al1)^2 - d4^2*cos(al3)^2 - pmz^2*cos(al1)^2 - d1^2*cos(al1)^2 + pmy^2*sin(al1)^2 + 2*d1*pmz*cos(al1)^2 - 2*d1*d4*cos(al1)*cos(al3) + 2*d4*pmz*cos(al1)*cos(al3))^(1/2) + d1*cos(al1)*1i + d4*cos(al3)*1i - pmz*cos(al1)*1i)/(pmx*sin(al1) - pmy*sin(al1)*1i))*1i
 -log(-((pmx^2*sin(al1)^2 - d4^2*cos(al3)^2 - pmz^2*cos(al1)^2 - d1^2*cos(al1)^2 + pmy^2*sin(al1)^2 + 2*d1*pmz*cos(al1)^2 - 2*d1*d4*cos(al1)*cos(al3) + 2*d4*pmz*cos(al1)*cos(al3))^(1/2) - d1*cos(al1)*1i - d4*cos(al3)*1i + pmz*cos(al1)*1i)/(pmx*sin(al1) - pmy*sin(al1)*1i))*1i




In [93]:
%%matlab_magic eng

syms pmx pmy pmz

Pm = [0 0 0 pmx; 0 0 0 pmy; 0 0 0 pmz; 0 0 0 1]; % posicion punto muñeca general
transl_zd4 =[0 0 0 0; 0 0 0 0; 0 0 0 d4; 0 0 0 1];

C1_left_mem = simplify(inv(T(:,:,1))) * Pm
C1_right_mem = T(:,:,2)*T(:,:,3)*transl_zd4
C1_left_mem(3,4)
C1_right_mem(3,4)

C1_left_mem =
[ 0, 0, 0,                                           pmx*cos(th1) - a1 + pmy*sin(th1)]
[ 0, 0, 0, pmz*sin(al1) - d1*sin(al1) + pmy*cos(al1)*cos(th1) - pmx*cos(al1)*sin(th1)]
[ 0, 0, 0, pmz*cos(al1) - d1*cos(al1) - pmy*sin(al1)*cos(th1) + pmx*sin(al1)*sin(th1)]
[ 0, 0, 0,                                                                          1]
C1_right_mem =
[ 0, 0, 0, d4*(sin(al3)*cos(th2)*sin(th3) + sin(al3)*cos(th3)*sin(th2)) + a2*cos(th2) + a3*cos(th2)*cos(th3) - a3*sin(th2)*sin(th3)]
[ 0, 0, 0, d4*(sin(al3)*sin(th2)*sin(th3) - sin(al3)*cos(th2)*cos(th3)) + a2*sin(th2) + a3*cos(th2)*sin(th3) + a3*cos(th3)*sin(th2)]
[ 0, 0, 0,                                                                                                              d4*cos(al3)]
[ 0, 0, 0,                                                                                                                        1]
ans =
pmz*cos(al1) - d1*cos(al1) - pmy*sin(al1)*cos(th1) + pmx*sin(al1)*sin(th1)
ans =
d4*c

In [63]:
%%matlab_magic eng

th1

th1 =
th1




In [38]:
%%matlab_magic eng

T03

T03 =
[ cos(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) - sin(th3)*(cos(th1)*sin(th2) + cos(al1)*cos(th2)*sin(th1)),   sin(al1)*sin(al3)*sin(th1) - cos(al3)*sin(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) - cos(al3)*cos(th3)*(cos(th1)*sin(th2) + cos(al1)*cos(th2)*sin(th1)), sin(al3)*cos(th3)*(cos(th1)*sin(th2) + cos(al1)*cos(th2)*sin(th1)) + sin(al3)*sin(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) + cos(al3)*sin(al1)*sin(th1), a1*cos(th1) - a3*sin(th3)*(cos(th1)*sin(th2) + cos(al1)*cos(th2)*sin(th1)) + a2*cos(th1)*cos(th2) + a3*cos(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) - a2*cos(al1)*sin(th1)*sin(th2)]
[ cos(th3)*(cos(th2)*sin(th1) + cos(al1)*cos(th1)*sin(th2)) - sin(th3)*(sin(th1)*sin(th2) - cos(al1)*cos(th1)*cos(th2)), - cos(al3)*cos(th3)*(sin(th1)*sin(th2) - cos(al1)*cos(th1)*cos(th2)) - cos(al3)*sin(th3)*(cos(th2)*sin(th1) + cos(al1)*cos(th1)*sin(th2)) - sin(al1)*sin(al3)*cos(th1), sin(al3)*cos(th3)*(sin(th1)*sin(th2) - cos(al1)*cos(th1)

In [84]:
%%matlab_magic eng

transf(1,4)
transf(2,4)
transf(3,4)

ans =
cos(th1)*(a1 + a3*cos(th2 + th3) + a2*cos(th2)) - d4*sin(th2 + th3)*cos(th1)
ans =
sin(th1)*(a1 + a3*cos(th2 + th3) + a2*cos(th2)) - d4*sin(th2 + th3)*sin(th1)
ans =
d1 - d4*cos(th2 + th3) - a3*sin(th2 + th3) - a2*sin(th2)




In [95]:
%%matlab_magic eng
exp1 =(pmx/cos(th1))-a2*cos(th2)-a1
expand(exp1^2)

exp1 =
pmx/cos(th1) - a1 - a2*cos(th2)
ans =
a2^2*cos(th2)^2 + pmx^2/cos(th1)^2 + a1^2 - (2*a1*pmx)/cos(th1) + 2*a1*a2*cos(th2) - (2*a2*pmx*cos(th2))/cos(th1)




In [96]:
%%matlab_magic eng
exp2 =d1-a2*sin(th2)-pmz
expand(exp2^2)

exp2 =
d1 - pmz - a2*sin(th2)
ans =
a2^2*sin(th2)^2 - 2*d1*pmz + d1^2 + pmz^2 - 2*a2*d1*sin(th2) + 2*a2*pmz*sin(th2)




In [ ]:
%%matlab_magic eng

[th1, th2, th3] = solve(pmx == eqs(1), pmy == eqs(2), pmz == eqs(3), [th1 th2 th3])

# Apéndice

Se muestra aquí el resultado completo en MATLAB de  $^0 T_6$:

In [90]:
%%matlab_magic eng
T06

T06 =
[ cos(th6)*(sin(th5)*(sin(al4)*(cos(al3)*(cos(al2)*sin(al1)*sin(th1) + sin(al2)*cos(th1)*sin(th2) + cos(al1)*sin(al2)*cos(th2)*sin(th1)) + sin(al3)*sin(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) + sin(al3)*cos(th3)*(cos(al2)*cos(th1)*sin(th2) - sin(al1)*sin(al2)*sin(th1) + cos(al1)*cos(al2)*cos(th2)*sin(th1))) + cos(al4)*sin(th4)*(sin(th3)*(cos(al2)*cos(th1)*sin(th2) - sin(al1)*sin(al2)*sin(th1) + cos(al1)*cos(al2)*cos(th2)*sin(th1)) - cos(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2))) - cos(al4)*cos(th4)*(cos(al3)*sin(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) - sin(al3)*(cos(al2)*sin(al1)*sin(th1) + sin(al2)*cos(th1)*sin(th2) + cos(al1)*sin(al2)*cos(th2)*sin(th1)) + cos(al3)*cos(th3)*(cos(al2)*cos(th1)*sin(th2) - sin(al1)*sin(al2)*sin(th1) + cos(al1)*cos(al2)*cos(th2)*sin(th1)))) - cos(th5)*(sin(th4)*(cos(al3)*sin(th3)*(cos(th1)*cos(th2) - cos(al1)*sin(th1)*sin(th2)) - sin(al3)*(cos(al2)*sin(al1)*sin(th1) + sin(al2)*cos(th1)*sin(th2) + cos(al1)*sin

La siguiente visualización solo está disponible si se visualiza y **ejecuta** en un kernel local.
<br><br>
A modo de curiosidad, se provee una herramienta interactiva que da la posición y orientacion de la punta del robot dadas las coordenadas articulares. Puede cambiar los valores de $\theta_i$ arrastrando con el ratón. De nuevo se insiste en ignorar el código y pasar a la visualización:

In [35]:
sls = [widgets.IntSlider(min=-180, max=180, step=10,  description=r"$\theta_{}$".format(i+1)) for i in range(6)]
# La sintaxis empleada no es muy pythonica, pero es la necesaria para interactuar con los widgets
ui = widgets.VBox(sls)
def modelo_directo(th1, th2, th3, th4, th5, th6):
    thetas = np.radians([th1,th2,th3,th4,th5,th6])
    coord = eng.eval("double(subs(T06, [th1, th2, th3, th4, th5, th6], {}))"
             .format(thetas))
    coord = np.array(coord)
    rot = Rot.from_matrix(coord[:3,:3]) # rotation matrix
    quat = rot.as_quat()                # rotation quaternion
    pos = coord[:3,3]                   # position vector
    with np.printoptions(formatter={'float': '{: 0.2f}'.format}):
        print("\nMatriz de rotación: \n", np.round(coord[:3,:3],2))
        print("\nRotacion en forma de quaternio: \n", np.round(quat,2))
        print("\nVector de posición absoluta: \n", np.round(pos, 2))

out = widgets.interactive_output(modelo_directo, {'th1': sls[0], 'th2': sls[1], 'th3': sls[2],
                                                  'th4': sls[3], 'th5': sls[4], 'th6': sls[5]})

display(ui, out)

Output()